In [779]:
import pandas as pd
import numpy as np

In [780]:
# импортируем и уберем непонятные пробелы
data = pd.read_excel('test.xlsx',converters={'Доходы':str,'Расходы':str})
data = data.applymap(lambda x: str(x).replace("\xa0", " ") if "\xa0" in str(x) else x)

In [781]:
#колонки мечты из образца
export_columns_names = ['Дата (дд/мм/гггг)','Категория','Плательщик', 'Счёт', 'Сумма (расход)', 'Счёт-получатель перевода', 'Сумма (доход)', 'Комментарий']

In [782]:
# давайте посмотрим на список все счетов, и проверим что не затесалось ничего лишнего
acc_names = data['Название'].dropna().unique()
acc_names, len(acc_names)

(array(['Кошелек', 'Альфабанк', 'Сбербанк', 'Tinkoff Black',
        'ВТБ - Банк москвы', 'Авангард', 'Альфабанк - Аэрофлот',
        'Альфабанк - EUR', 'АльфаБанк - GBP', 'Альфабанк - USD',
        'Наличные - USD', 'Наличные - EUR', 'Альфа-директ',
        'АльфаДирект - USD', 'Поток - АльфаГрупп', 'СмартВклад RUB',
        'Tinkoff Platinum'], dtype=object), 17)

In [801]:
for each in acc_names:
    print(each)

Кошелек
Альфабанк
Сбербанк
Tinkoff Black
ВТБ - Банк москвы
Авангард
Альфабанк - Аэрофлот
Альфабанк - EUR
АльфаБанк - GBP
Альфабанк - USD
Наличные - USD
Наличные - EUR
Альфа-директ
АльфаДирект - USD
Поток - АльфаГрупп
СмартВклад RUB
Tinkoff Platinum


In [783]:
#выбираем все строки в которых счетом указан "Кошелек"
data.loc[data['Счет'] == 'Кошелек']

Название Текущий баланс     Счет             Трансферы  \
1        NaN            NaN  Кошелек                   NaN   
2        NaN            NaN  Кошелек                   NaN   
3        NaN            NaN  Кошелек                   NaN   
4        NaN            NaN  Кошелек                   NaN   
5        NaN            NaN  Кошелек         Tinkoff Black   
6        NaN            NaN  Кошелек                   NaN   
7        NaN            NaN  Кошелек         Tinkoff Black   
8        NaN            NaN  Кошелек                   NaN   
9        NaN            NaN  Кошелек              Авангард   
10       NaN            NaN  Кошелек         Tinkoff Black   
11       NaN            NaN  Кошелек                   NaN   
12       NaN            NaN  Кошелек                   NaN   
13       NaN            NaN  Кошелек                   NaN   
14       NaN            NaN  Кошелек         Tinkoff Black   
15       NaN            NaN  Кошелек                   NaN   
16       NaN            NaN  Кошелек                   NaN   
17       NaN            NaN  Кошелек                   NaN   
18       NaN            NaN  Кошелек                   NaN   
19       NaN            NaN  Кошелек         Tinkoff Black   
20       NaN            NaN  Кошелек  Альфабанк - Аэрофлот   
21       NaN            NaN  Кошелек                   NaN   
22       NaN            NaN  Кошелек                   NaN   
23       NaN            NaN  Кошелек  Альфабанк - Аэрофлот   
24       NaN            NaN  Кошелек         Tinkoff Black   
25       NaN            NaN  Кошелек  Альфабанк - Аэрофлот   
26       NaN            NaN  Кошелек                   NaN   
27       NaN            NaN  Кошелек                   NaN   
28       NaN            NaN  Кошелек                   NaN   
29       NaN            NaN  Кошелек         Tinkoff Black   
30       NaN            NaN  Кошелек                   NaN   
..       ...            ...      ...                   ...   
953      NaN            NaN  Кошелек             Альфабанк   
954      NaN            NaN  Кошелек                   NaN   
955      NaN            NaN  Кошелек                   NaN   
956      NaN            NaN  Кошелек                   NaN   
957      NaN            NaN  Кошелек                   NaN   
958      NaN            NaN  Кошелек                   NaN   
959      NaN            NaN  Кошелек      Tinkoff Platinum   
960      NaN            NaN  Кошелек                   NaN   
961      NaN            NaN  Кошелек              Авангард   
962      NaN            NaN  Кошелек                   NaN   
963      NaN            NaN  Кошелек                   NaN   
964      NaN            NaN  Кошелек                   NaN   
965      NaN            NaN  Кошелек         Tinkoff Black   
966      NaN            NaN  Кошелек                   NaN   
967      NaN            NaN  Кошелек                   NaN   
968      NaN            NaN  Кошелек                   NaN   
969      NaN            NaN  Кошелек     ВТБ - Банк москвы   
970      NaN            NaN  Кошелек                   NaN   
971      NaN            NaN  Кошелек         Tinkoff Black   
972      NaN            NaN  Кошелек         Tinkoff Black   
973      NaN            NaN  Кошелек      Tinkoff Platinum   
974      NaN            NaN  Кошелек                   NaN   
975      NaN            NaN  Кошелек         Tinkoff Black   
976      NaN            NaN  Кошелек                   NaN   
977      NaN            NaN  Кошелек                   NaN   
978      NaN            NaN  Кошелек              Сбербанк   
979      NaN            NaN  Кошелек      Tinkoff Platinum   
980      NaN            NaN  Кошелек                   NaN   
981      NaN            NaN  Кошелек                   NaN   
982      NaN            NaN  Кошелек                   NaN   

                                 Описание         Контрагент  \
1                           автомойка киа          Автомойка   
2                              

In [784]:
#делаем дата фрейм только с операциями по всем счетам, выкидываем балансы и названия больших столбцов
new_df = pd.DataFrame(columns=data.columns)
for each_acc_name in acc_names:
    new_df = new_df.append(data.loc[data['Счет'] == each_acc_name])

In [785]:
#сортируем по дате и внутри даты по времени
new_df = new_df.sort_values(['Дата','Время'], ascending=[False,False])
new_df = new_df.reset_index(drop=True)
new_df

Название Текущий баланс                  Счет           Трансферы  \
0         NaN            NaN          Альфа-директ                 NaN   
1         NaN            NaN               Кошелек                 NaN   
2         NaN            NaN               Кошелек                 NaN   
3         NaN            NaN  Альфабанк - Аэрофлот                 NaN   
4         NaN            NaN  Альфабанк - Аэрофлот                 NaN   
5         NaN            NaN  Альфабанк - Аэрофлот                 NaN   
6         NaN            NaN  Альфабанк - Аэрофлот                 NaN   
7         NaN            NaN  Альфабанк - Аэрофлот                 NaN   
8         NaN            NaN              Авангард                 NaN   
9         NaN            NaN  Альфабанк - Аэрофлот                 NaN   
10        NaN            NaN             Альфабанк       Tinkoff Black   
11        NaN            NaN         Tinkoff Black           Альфабанк   
12        NaN            NaN             Альфабанк  Поток - АльфаГрупп   
13        NaN            NaN    Поток - АльфаГрупп           Альфабанк   
14        NaN            NaN               Кошелек                 NaN   
15        NaN            NaN               Кошелек                 NaN   
16        NaN            NaN  Альфабанк - Аэрофлот                 NaN   
17        NaN            NaN  Альфабанк - Аэрофлот                 NaN   
18        NaN            NaN  Альфабанк - Аэрофлот                 NaN   
19        NaN            NaN  Альфабанк - Аэрофлот                 NaN   
20        NaN            NaN         Tinkoff Black   ВТБ - Банк москвы   
21        NaN            NaN     ВТБ - Банк москвы       Tinkoff Black   
22        NaN            NaN               Кошелек       Tinkoff Black   
23        NaN            NaN         Tinkoff Black             Кошелек   
24        NaN            NaN         Tinkoff Black            Авангард   
25        NaN            NaN              Авангард       Tinkoff Black   
26        NaN            NaN              Сбербанк                 NaN   
27        NaN            NaN              Сбербанк       Tinkoff Black   
28        NaN            NaN         Tinkoff Black            Сбербанк   
29        NaN            NaN             Альфабанк            Сбербанк   
...       ...            ...                   ...                 ...   
4744      NaN            NaN             Альфабанк                 NaN   
4745      NaN            NaN             Альфабанк                 NaN   
4746      NaN            NaN             Альфабанк                 NaN   
4747      NaN            NaN      Tinkoff Platinum                 NaN   
4748      NaN            NaN             Альфабанк                 NaN   
4749      NaN            NaN             Альфабанк                 NaN   
4750      NaN            NaN             Альфабанк                 NaN   
4751      NaN            NaN             Альфабанк                 NaN   
4752      NaN            NaN             Альфабанк                 NaN   
4753      NaN            NaN      Tinkoff Platinum                 NaN   
4754      NaN            NaN      Tinkoff Platinum                 NaN   
4755      NaN            NaN      Tinkoff Platinum                 NaN   
4756      NaN            NaN             Альфабанк                 NaN   
4757      NaN            NaN      Tinkoff Platinum                 NaN   
4758      NaN            NaN      Tinkoff Platinum                 NaN   
4759      NaN            NaN      Tinkoff Platinum                 NaN   
4760      NaN            NaN      Tinkoff Platinum                 NaN   
4761      NaN            NaN      Tinkoff Platinum                 NaN   
4762      NaN            NaN      Tinkoff Platinum                 NaN   
4763      NaN            NaN      Tinkoff Platinum                 NaN   
4764      NaN            NaN      Tinkoff Platinum                 NaN   
4765      NaN            NaN      Tinkoff Platinum                 NaN   
4766     

1. Установить однозначное соответствие между колонками
2. Смерджить 2 операции трансфера в одну
3. Экспортировать CSV (с нарезкой по кусочкам)
4. импортировать и проверить баланс


In [786]:
def notTranfer(row):
    #проверяем не является ли строчка трансфером. True - не является. False - это трансфер
    if pd.isna(row['Трансферы']):
        return True
    else:
        return False

In [787]:
def notCoveredTransfer(row):
    if pd.isna(row['Название']):
        return True
    else:
        return False

In [788]:
def setAsMarked(row_num):
    new_df.at[row_num,'Название'] = 'transfer'   

In [789]:
def exportDf(row):
    date = row['Дата']
    category = row['Категория']
    payer = row['Контрагент']
    acc1 = np.nan
    acc2 = np.nan
    minus_summ = np.nan
    plus_summ = np.nan
    if pd.isna(row['Доходы']):
        acc1 = row['Счет']
        minus_summ = row['Расходы'].replace(" ",'').replace(".",',')
    else:
        acc2 = row['Счет']
        plus_summ = row['Доходы'].replace(" ",'').replace(".",',')
    comment = row['Описание']
    return pd.DataFrame([[date, category, payer, acc1, minus_summ, acc2, plus_summ, comment]], columns=export_columns_names)
    #return date, category, payer,acc1, minus_summ, acc2, plus_summ, comment
exportDf(new_df.loc[0]).to_csv('test.csv', sep=';', index = False)

In [790]:
new_df.loc[10:11]

Название Текущий баланс           Счет      Трансферы  \
10      NaN            NaN      Альфабанк  Tinkoff Black   
11      NaN            NaN  Tinkoff Black      Альфабанк   

                         Описание Контрагент Категория       Дата     Время  \
10  Перевод на счет Tinkoff Black        NaN       NaN 2018-09-06  13:43:00   
11      Перевод со счет Альфабанк        NaN       NaN 2018-09-06  13:43:00   

   Памятка    Доходы    Расходы Валюта Номер чека Теги      Баланс  
10     NaN       NaN  -3 208,15    RUB        NaN  NaN           0  
11     NaN  3 208,15        NaN    RUB        NaN  NaN  +21 644,06

In [791]:
def checkSum(row1, row2):
    if not pd.isna(row1['Расходы']):
        return row1['Расходы'].replace('-','').replace(' ','').replace('.',',') == row2['Доходы'].replace(" ","").replace(".",',')
    else:
        return row2['Расходы'].replace('-','').replace(' ','').replace('.',',') == row1['Доходы'].replace(" ","").replace(".",',')

In [792]:
def getPair(index):
    row = new_df.loc[index]
    if not pd.isna(row['Расходы']):
        answer = new_df.loc[(new_df['Счет'] == row['Трансферы']) 
                            & (new_df['Трансферы'] == row['Счет']) 
                            & (new_df['Дата'] == row['Дата']) 
                            & (new_df['Время'] == row['Время']) 
                            & ((row['Расходы'].replace('-','') == new_df['Доходы']) | (row['Валюта'] != new_df['Валюта']))
                            & (new_df['Название'] != 'transfer')
                           ]
    else:
        answer = new_df.loc[(new_df['Счет'] == row['Трансферы']) 
                            & (new_df['Трансферы'] == row['Счет']) 
                            & (new_df['Дата'] == row['Дата']) 
                            & (new_df['Время'] == row['Время']) 
                            & ((new_df['Расходы'] == '-'+row['Доходы']) | (row['Валюта'] != new_df['Валюта']))
                            & (new_df['Название'] != 'transfer') 
                           ]
    if len(answer.index) > 1:
        print("AHTUNG", answer.index, end =' ')
    return answer.index[0]

In [793]:
getPair(59)

60

In [794]:
def createTransferOperation(index1, index2):
    row1 = new_df.loc[index1]
    row2 = new_df.loc[index2]
    date = row1['Дата']
    category = np.nan
    payer = np.nan
    if pd.isna(row1['Доходы']):
        acc1 = row1['Счет']
        minus_summ = row1['Расходы'].replace(" ",'').replace(".",',')
        acc2 = row2['Счет']
        plus_summ = row2['Доходы'].replace(" ",'').replace(".",',')
    else:
        acc1 = row2['Счет']
        minus_summ = row2['Расходы'].replace(" ",'').replace(".",',')
        acc2 = row1['Счет']
        plus_summ = row1['Доходы'].replace(" ",'').replace(".",',')
    comment = row1['Описание'] + ' ' +row2['Описание']
    return pd.DataFrame([[date, category, payer, acc1, minus_summ, acc2, plus_summ, comment]], columns=export_columns_names)

createTransferOperation(11,10)

Дата (дд/мм/гггг)  Категория  Плательщик       Счёт Сумма (расход)  \
0        2018-09-06        NaN         NaN  Альфабанк       -3208,15   

  Счёт-получатель перевода Сумма (доход)  \
0            Tinkoff Black       3208,15   

                                         Комментарий  
0  Перевод со счет Альфабанк Перевод на счет Tink...

In [795]:
new_df.at[2078,'Время'] = new_df.iloc[2077]['Время']

In [796]:
new_df.iloc[2077:2100]

Название Текущий баланс                  Счет        Трансферы  \
2077      NaN            NaN             Альфабанк  Альфабанк - EUR   
2078      NaN            NaN       Альфабанк - EUR        Альфабанк   
2079      NaN            NaN  Альфабанк - Аэрофлот              NaN   
2080      NaN            NaN              Сбербанк              NaN   
2081      NaN            NaN              Сбербанк              NaN   
2082      NaN            NaN  Альфабанк - Аэрофлот              NaN   
2083      NaN            NaN              Сбербанк              NaN   
2084      NaN            NaN  Альфабанк - Аэрофлот              NaN   
2085      NaN            NaN              Авангард              NaN   
2086      NaN            NaN               Кошелек    Tinkoff Black   
2087      NaN            NaN         Tinkoff Black          Кошелек   
2088      NaN            NaN      Tinkoff Platinum              NaN   
2089      NaN            NaN  Альфабанк - Аэрофлот              NaN   
2090      NaN            NaN               Кошелек              NaN   
2091      NaN            NaN               Кошелек              NaN   
2092      NaN            NaN  Альфабанк - Аэрофлот              NaN   
2093      NaN            NaN      Tinkoff Platinum              NaN   
2094      NaN            NaN      Tinkoff Platinum              NaN   
2095      NaN            NaN         Tinkoff Black              NaN   
2096      NaN            NaN         Tinkoff Black              NaN   
2097      NaN            NaN      Tinkoff Platinum              NaN   
2098      NaN            NaN              Авангард  Альфабанк - USD   
2099      NaN            NaN       Альфабанк - USD         Авангард   

                             Описание      Контрагент  \
2077              комиссия за февраль             NaN   
2078              комиссия за февраль             NaN   
2079                   Еда вода бухло  Красная Поляна   
2080           Социальное обеспечение             СВР   
2081           Социальное обеспечение             СВР   
2082                            Маска           Scott   
2083           Социальное обеспечение             СВР   
2084                     ски-пасс 3+1      Роза Хутор   
2085                      Информатика    Омар Хасанов   
2086      Снятие наличных в банкоматe             NaN   
2087      Снятие наличных в банкоматe             NaN   
2088                           music          itunes   
2089                    чехол для лыж      ADC ACTIVE   
2090                    Аэропорт сочи     Такси Везет   
2091                         Аэропорт     Такси Везет   
2092                 МСК - СОЧИ - МСК     S7 Airlines   
2093                          бабушка         Мегафон   
2094                         заправка              BP   
2095          смс-банк + обслуживание         Tinkoff   
2096                    Cash back + %         Tinkoff   
2097                йогурт и печеньки   7ой континент   
2098  Перевод со счет Альфабанк - USD             NaN   
2099         Перевод на счет Авангард             NaN   

                           Категория       Дата     Время Памятка     Доходы  \
2077                             NaN 2017-02-06  16:01:00     NaN     179.49   
2078                             NaN 2017-02-06  16:01:00     NaN        NaN   
2079  Путешествия > Кафе и рестораны 2017-02-05  16:17:00     NaN        NaN   
2080                  Secret Service 2017-02-04  12:00:00     NaN   1 906,90   
2081                  Secret Service 2017-02-04  12:00:00     NaN   4 215,90   
2082    Досуг > Спортивный инвентарь 2017-02-03  16:16:00     NaN        NaN   
2083                  Secret Service 2017-02-03  12:00:00     NaN  10 446,25   
2084       Путешествия > Развлечения 2017-02-02  16:06:00     NaN        NaN   
2085                         Ученики 2017-02-02  12:03:00     NaN   2 000,00   
2086                             NaN 2017-02-01  16:01:00     NaN   4 900,00   
2087                             NaN 2017-02-01  16

In [797]:
export_df = pd.DataFrame(columns=export_columns_names)

for i in range(len(new_df)):
    row = new_df.loc[i]
    if notTranfer(row):
        export_df = export_df.append(exportDf(row))
    elif notCoveredTransfer(row):
        index1 = i
        print(i, end=' ')
        index2 = getPair(i)
        print(index2)
        setAsMarked(index1)
        setAsMarked(index2)
        export_df = export_df.append(createTransferOperation(index1,index2))
    else:
        #print(i, "I don't know what's this")#остальное значит обработанный трансфер и реагировать не надо
        pass
        

10 11
12 13
20 21
22 23
24 25
27 28
29 30
31 32
33 34
46 47
48 49
50 51
52 53
57 58
59 60
61 62
65 66
76 77
78 79
83 85
90 93
91 92
94 95
100 101
103 106
104 107
105 108
109 110
128 129
131 133
132 134
136 137
149 150
151 152
153 154
170 171
172 173
174 175
176 177
189 190
194 196
197 198
211 212
234 235
247 248
249 251
250 252
253 254
257 258
282 283
284 285
295 298
296 297
299 300
304 305
307 308
317 318
333 335
334 337
338 339
346 347
361 362
363 364
378 379
380 381
386 388
389 390
399 400
402 403
409 410
412 413
419 420
456 457
458 459
464 466
465 467
489 490
497 498
510 511
525 526
535 536
537 538
540 543
567 568
570 571
573 575
574 576
589 590
595 596
597 598
599 600
602 603
604 605
606 607
608 609
619 620
621 622
625 626
634 635
636 639
637 638
642 645
643 644
646 647
654 655
656 658
659 660
671 672
674 675
689 690
692 693
700 701
704 705
706 707
714 717
718 720
719 721
732 733
734 735
736 737
739 740
743 745
746 747
750 751
752 753
761 762
768 769
771 772
779 780
781 782
783 78

4444 4445
4448 4449
4459 4460
4463 4464
4467 4470
4468 4469
4471 4472
4476 4477
4478 4479
4480 4481
4482 4483
4485 4486
4527 4528
4529 4530
4531 4532
4533 4534
4538 4539
4554 4555
4556 4557
4558 4559
4570 4572
4571 4573
4574 4575
4576 4577
4580 4581
4586 4587
4594 4596
4595 4597
4612 4613
4616 4617
4618 4619
4620 4621
4628 4629
4642 4643
4658 4660
4664 4667
4665 4666
4673 4676
4674 4675
4681 4682
4694 4695
4701 4703
4702 4704
4705 4706
4710 4711
4714 4715
4716 4717


In [803]:
export_df.to_csv('full.csv',index=False,sep=';',header=False)

In [799]:
len(export_df)

3886

def writeExportFile(from_num, to_num):
    export_df.iloc[from_num:to_num].to_csv(str(from_num)+'!'+str(to_num)+'.csv',sep=';',index=False, header = False)


step = 500
from_num = 0
to_num = step

while True:
    if to_num >= len(export_df):
        writeExportFile(from_num, len(export_df))
        break
    else:
        writeExportFile(from_num,to_num)
    from_num += step
    to_num += step
    "